In [1]:
from __future__ import print_function
import matplotlib.pyplot as plt # librairie de plot
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
import numpy as np
import numpy.random as ran
import seaborn as sns

def un(x):
    return 1.0

# Comparison SIR Models

In previous notebook we have introduce the SIR model with ODE. There are **stochastic versions** of SIR type models.

In this note book we propose to compare deterministic and stochastic SIR models

## Deterministic SIR model death/birth process 

We consider four functions: susceptible peoples $S(t)$, exposed peoples $E(t)$ ,infectious peoples $I(t)$ and retired peoples $R(t)$. The dynamic is described by

\begin{align}
\dot{S}(t) & = -\beta \frac{S(t)I(t)}{N(t)}   \\
\dot{I}(t) & = \beta \frac{S(t)I(t)}{N(t)}  \\
\dot{R}(t) & = \gamma I(t)
\end{align}

with $N(t)=S(t)+I(t)+R(t)$ the total population.

## Stochastic SIR model death/birth process

In the stochastic version the model SIR is described by a **Markok process**. We consider a population
$$
\mathbf{X}_n= (S_n,I_n,R_n)
$$

The Markov process described how transit to another state $\mathbf{X}_{n+1}= (S_{n+1},I_{n+1},R_{n+1})$.

Indeed the populations at a step $n+1$ depend only of the population. In a population modeling the information useful for predicting the future is entirely contained in the present state of the process and is not dependent on past states (the system has no "memory"). It is why we consider Markov process. 

For this model it is equivalent to

$$
\mathbb{P}(\mathbf{X}_n= (S_n,I_n,R_n) | \mathbf{X}_0= (S_0,I_0,R_0),.. ,\mathbf{X}_{n-1}= (S_{n-1},I_{n-1},R_{n-1}))
$$
$$
 = \mathbb{P}(\mathbf{X}_n= (S_n,I_n,R_n) | \mathbf{X}_{n-1}= (S_{n-1},I_{n-1},R_{n-1})) 
$$

To define this **Markov process** we wiil begin to define a caracteristic time $\Delta_t$ during which there is, at best, **one** change of state.
 
Since the population is constant we define the Marok process only on $S$ and $I$.
Now we will define the matrix transition which define possible future states and there probabilities:

 - $\mathbb{P}(\mathbf{X}_{n+1}= (S_n-1,I_n+1) | \mathbf{X}_{n}= (S_{n},I_{n})) = \beta \frac{S_nI_n}{N}\Delta_t$
 - $\mathbb{P}(\mathbf{X}_{n+1}= (S_n,I_n-1) | \mathbf{X}_{n}= (S_{n},I_{n})) = \gamma I_n \Delta_t$
 - $\mathbb{P}(\mathbf{X}_{n+1}= (S_n,I_n) | \mathbf{X}_{n}= (S_{n},I_{n})) = 1-\beta \frac{S_nI_n}{N}\Delta_t-\gamma I_n \Delta_t$

### Advantage

There is, in a epidemic, a part of random. For example the creation of "cluster" seems unpredictible.
Additionnally an epidemic can anslo never begin if the first patient never infect other peoples.

The stochastic model are able to deal with that and are more useful to make uncertitude analysis.

## Numerical scheme

For the deterministic model we use the same numerical scheme as before. It is a **forward Euler scheme**.
For the stochastic model we use a classical Markov process simulation. The time step is choosen very small.

We use an **unform probability law** for transition matrix.


In [2]:
def DSIR(S0=999,I0=1,beta=0.7,gamma=0.3,ft=80):
    S = [S0] ; I = [I0]; R = [0.0]
    N = S[-1]+I[-1]+R[-1]
    R0 = beta/gamma
    Rt = [R0*S[-1]/N]
    times =[0.0];  dt = 0.1
    
    while times[-1]<float(ft):
        Snp = S[-1] - dt*beta*S[-1]*I[-1]/N             
        Inp = I[-1] + dt*beta*S[-1]*I[-1]/N -dt*gamma*I[-1]
        Rnp = R[-1] + dt*gamma*I[-1]
        times.append(times[-1]+dt)
        S.append(Snp)            
        I.append(Inp)
        R.append(Rnp)
        Rt.append(R0*(Snp/N))
        
    return times,Rt,S,I,R

In [5]:
def SSIR(S0=999,I0=1,beta=0.7,gamma=0.3,ft=80):
    S = [S0] ; I = [I0]; R = [0.0]
    N = S[-1]+I[-1]+R[-1]
    R0 = beta/gamma
    Rt = [R0*S[-1]/N]
    times =[0.0];  dt = 0.002
    
    while times[-1]<float(ft):
        p1 = beta*S[-1]*I[-1]/N*dt
        p2 = p1 + gamma*I[-1]*dt
        u = ran.uniform(0.0,1.0)
        if u < p1:
            Snp = S[-1]-1
            Inp = I[-1]+1
        elif u < p2:
            Snp = S[-1]
            Inp = I[-1]-1
        else:
            Snp = S[-1]
            Inp = I[-1]
            
        Rnp = N- Snp-Inp
        times.append(times[-1]+dt)
        S.append(Snp)            
        I.append(Inp)
        R.append(Rnp)
        Rt.append(R0*(Snp/N))
    return times,Rt,S,I,R  

## Numerical results and comparison

In [6]:
def CompareSIR(S0=999,I0=1,beta=0.7,gamma=0.3,nba=1,ft=50):
    
    Dt,DRt,DS,DI,DR = DSIR(S0,I0,beta,gamma,ft)
    sns.set_palette("Spectral",10)

    plt.figure(figsize=(9,7))
    ax1 =plt.subplot(221)
    ax2 =plt.subplot(222)
    ax3 =plt.subplot(212)
    for i in range(0,int(nba)):
        St,SRt,SS,SI,SR = SSIR(S0,I0,beta,gamma,ft)
        ax1.plot(St, SR) 
        ax2.plot(St, SRt) 
        ax3.plot(St, SI) 
     
    ax1.plot(Dt, DR,  color='black') 
    ax2.plot(Dt, DRt,  color='black') 
    ax3.plot(Dt, DI, color='black')
    plt.show()

In [7]:
S0 = widgets.IntText(value=1000,description="S0")
I0 = widgets.IntText(value=1,description="I0")
b1 = widgets.HBox([S0,I0])

beta = widgets.FloatSlider(value=0.7,min=0.01,max=1.0,step=0.02,description="beta")
gamma = widgets.FloatSlider(value=0.3,min=0.01,max=1.0,step=0.02,description="gamma")
b2 = widgets.HBox([beta,gamma])

nba = widgets.IntSlider(value=1,min=1,max=20,step=1,description="Nb simulation")
ft = widgets.IntText(value=80,description="Final time")
b3 = widgets.HBox([nba,ft])

ui= widgets.VBox([b1,b2,b3])
out = widgets.interactive_output(CompareSIR, {'S0': S0, 'I0': I0, 'beta': beta, 'gamma': gamma,\
                                              "nba": nba, "ft": ft})

In [8]:
display(ui,out)

Output(outputs=({'output_type': 'display_data', 'data': {'text/plain': '<Figure size 648x504 with 3 Axes>', 'i…